# Mexican Senate Data

## Importing necessary libraries

In [1]:
# importing required modules
import requests
import pandas as pd
import seaborn as sns
from bs4 import BeautifulSoup
import numpy as np
from lxml import etree
import re
from selenium import webdriver
import time

## Senator Database, Exports to CSV in data folder.

### Importing senator table

In [2]:
def get_senators():
    senators_url = 'https://www.senado.gob.mx/65/datosAbiertos/senadoresDatosAb.json'
    senators_json = requests.get(senators_url).json()
    senators = pd.DataFrame.from_dict(senators_json)
    senators = senators.rename(columns={"idSenador": "senator_id"})
    return senators

In [203]:
senators = get_senators()

In [204]:
#Creating a field that includes first and last names to join with initiatives+proposals table.
senators["senadores"] = senators["Nombre"].str.strip()+" "+senators["Apellidos"].str.strip()

### Importing attendance data and adding to senator table

In [5]:
def get_senator_attendance():
    
    senators = get_senators()
    
    senator_ids = senators["senator_id"].tolist()
    
    senator_attendance = pd.DataFrame()
    senator_attendance["senator_id"] = ""
    senator_attendance["session_date"] = ""
    senator_attendance["attendance_record"] = ""

    counter = 0
    for sen in senator_ids:
        url = f'https://www.senado.gob.mx/65/asistencias/{sen}#info'
        html = requests.get(url)
        content = BeautifulSoup(html.text, 'html.parser')
        content_x = etree.HTML(str(content))
        dates = content_x.xpath('//*[@id="imPage"]/div[7]/div[2]/div/div[2]/section/div/div/table/tbody//a')
        att_records = content_x.xpath('//*[@id="imPage"]/div[7]/div[2]/div/div[2]/section/div/div/table/tbody//strong')
        for i in range(len(dates)):
            senator_attendance.at[i+counter, 'senator_id'] = sen
            senator_attendance.at[i+counter, 'session_date'] = dates[i].text
            senator_attendance.at[i+counter, 'attendance_record'] = att_records[i].text
        counter += len(dates)

    senator_attendance["attendance_score"] = senator_attendance["attendance_record"].copy()
    senator_attendance["attendance_score"] = senator_attendance["attendance_score"].map(lambda x: 1 if x == "Asistencia" else 0)
    senator_attendance = pd.merge(senator_attendance, senators[['senator_id','Fraccion', 'Estado', 'Apellidos', 'Nombre', 'tipoEleccion']], on='senator_id', how='left')

    senator_attendance["full_name"] = senator_attendance['Nombre'] + " " + senator_attendance['Apellidos']
    
    senator_attendance = senator_attendance.groupby(['senator_id', 'full_name', 'Fraccion', 'Estado', 'tipoEleccion'], as_index=False)[['attendance_score']].mean()

    return senator_attendance

In [6]:
senator_attendance = get_senator_attendance()

In [205]:
senators = senators.merge(senator_attendance[["senator_id", "attendance_score"]], how="left", on="senator_id")

### Importing initiatives and proposals, concatenating both and adding senator ids

In [8]:
def get_initiatives():
    """fucntion that extracts initiatives from Senate JSON."""
    
    init_64_url = 'https://www.senado.gob.mx/65/datosAbiertos/iniciativa_64.json'
    init_65_url = 'https://www.senado.gob.mx/65/datosAbiertos/iniciativa_65.json'
    
    init_64_json = requests.get(init_64_url).json()
    init_65_json = requests.get(init_65_url).json()
    
    init_64 = pd.DataFrame.from_dict(init_64_json)
    init_65 = pd.DataFrame.from_dict(init_65_json)
    
    initiatives = pd.concat([init_64, init_65])
    
    initiatives['fecha_presentacion'] = pd.to_datetime(initiatives['fecha_presentacion'],errors='coerce')
    initiatives['fecha_aprobacion'] = pd.to_datetime(initiatives['fecha_aprobacion'],errors='coerce')
    
    initiatives = initiatives.set_index('id')
        
    return initiatives

In [9]:
def get_proposals():
    """fucntion that extracts proposals from Senate JSON."""
    
    prop_64_url = 'https://www.senado.gob.mx/65/datosAbiertos/proposicion_64.json'
    prop_65_url = 'https://www.senado.gob.mx/65/datosAbiertos/proposicion_65.json'
    
    prop_64_json = requests.get(prop_64_url).json()
    prop_65_json = requests.get(prop_65_url).json()
    
    prop_64 = pd.DataFrame.from_dict(prop_64_json)
    prop_65 = pd.DataFrame.from_dict(prop_65_json)
    
    proposals = pd.concat([prop_64, prop_65])
    
    proposals['fecha_presentacion'] = pd.to_datetime(proposals['fecha_presentacion'],errors='coerce')
    proposals['fecha_aprobacion'] = pd.to_datetime(proposals['fecha_aprobacion'],errors='coerce')
    
    proposals = proposals.set_index('id')
    
    return proposals

In [244]:
#Create concatenated df that includes initiatives and proposals.
initiatives = get_initiatives()
proposals = get_proposals()
inipros = pd.concat([initiatives, proposals])

In [25]:
print(f"Inipros df has {inipros.shape[0]} initiatives with {inipros.shape[1]} features.")

Inipros df has 9396 initiatives with 13 features.


In [245]:
#creates a 1:1 relationship between initiative/proposal and senator (in case where more than 1 senator proposes).
inipros["senadores"] = inipros["senadores"].apply(lambda x:x.strip().split("<br>"))

for i, row in inipros.iterrows():
    senator_ids = []
    for senator in row["senadores"]:
        strt_pos = senator.find('(')
        senator = senator[:strt_pos-1].strip()
        senator_ids.append(senator)
    inipros.at[i, "senadores"] = senator_ids[:-1]

inipros = inipros.explode("senadores")

In [246]:
#Manually change names in inipros so they match senator names from senator table.

inipros.loc[inipros["senadores"] == "Geovanna del Carmen Bañuelos de La Torre", "senadores"] = "Geovanna Bañuelos"
inipros.loc[inipros["senadores"] == "Noé Fernando Castañón Ramírez", "senadores"] = "Noé Castañón"
inipros.loc[inipros["senadores"] == "José Clemente Castañeda Hoeflich", "senadores"] = "Clemente Castañeda Hoeflich"
inipros.loc[inipros["senadores"] == "Juan Manuel Zepeda Hernández", "senadores"] = "Juan Zepeda"
inipros.loc[inipros["senadores"] == "Patricia Mercado Castro", "senadores"] = "Patricia Mercado"
inipros.loc[inipros["senadores"] == "Dante Delgado Rannauro", "senadores"] = "Dante Delgado"
inipros.loc[inipros["senadores"] == "Bertha Xóchitl Gálvez Ruiz", "senadores"] = "Xóchitl Gálvez Ruiz"
inipros.loc[inipros["senadores"] == "Lilly Téllez García", "senadores"] = "Lilly Téllez"
inipros.loc[inipros["senadores"] == "Raúl Bolaños Cacho Cué", "senadores"] = "Raúl Bolaños-Cacho Cué"
inipros.loc[inipros["senadores"] == "Elvia Marcela Mora Arellano", "senadores"] = "Marcela Mora"
inipros.loc[inipros["senadores"] == "Minerva Citlalli Hernández Mora", "senadores"] = "M. Citlalli Hernández Mora"

In [247]:
#Inner join on senator names to ensure only initiatives that match senator ids from table remain.
inipros = inipros.merge(senators[["senadores", "senator_id"]], how='left', on='senadores')

In [248]:
print(f"Inipros df has {inipros.shape[0]} initiatives with {inipros.shape[1]} features.")

Inipros df has 12828 initiatives with 14 features.


In [249]:
print(f"Inipros df has {inipros.shape[0]} initiatives with {inipros.shape[1]} features.")

Inipros df has 12828 initiatives with 14 features.


### Create columns for initiatives by commission

In [250]:
#Create a clean list of commissions to which each initiative belongs

inipros["comisiones"] = inipros["comisiones"].apply(lambda x:x.split("<br>")[1].strip() 
                                                    if "Puntos Constitucionales" in x and not x.split("<br>")[1] == ""
                                                    else x.split("<br>")[0].strip())

inipros["comisiones"] = inipros["comisiones"].apply(lambda x:x.split(", ") if "Comisión" in x else x)

inipros = inipros.explode("comisiones")

inipros["comisiones"] = inipros["comisiones"].apply(lambda x:x.replace("(Coordinadora)", ""))
inipros["comisiones"] = inipros["comisiones"].apply(lambda x:x.replace("Tercera Comisión:", ""))
inipros["comisiones"] = inipros["comisiones"].apply(lambda x:x.replace("Segunda Comisión:", ""))
inipros["comisiones"] = inipros["comisiones"].apply(lambda x:x.replace("Primera Comisión:", "").strip())
inipros["comisiones"] = inipros["comisiones"].apply(lambda x:x.replace("(Comisiones Unidas)", "").strip())


inipros["comisiones"] = inipros["comisiones"].apply(lambda x:x.split(" y ") if "Defensa Nacional y Educación Pública" in x else x)

inipros = inipros.explode("comisiones")

inipros["comisiones"] = inipros["comisiones"].apply(lambda x:"Relaciones Exteriores".strip() if "Relaciones Exteriores" in x else x)
inipros["comisiones"] = inipros["comisiones"].apply(lambda x:"Educación".strip() if "Educación" in x else x)
inipros["comisiones"] = inipros["comisiones"].apply(lambda x:"Justicia".strip() if "Justicia" in x else x)
inipros["comisiones"] = inipros["comisiones"].apply(lambda x:"Seguridad Social".strip() if "Social" in x else x)
inipros["comisiones"] = inipros["comisiones"].apply(lambda x:"Agricultura, Ganadería, Pesca y Desarrollo Rural".strip() if "Agr" in x else x)
inipros["comisiones"] = inipros["comisiones"].apply(lambda x:"Energía".strip() if "Recursos Hidráulicos" in x else x)
inipros["comisiones"] = inipros["comisiones"].apply(lambda x:"Estudios Legislativos".strip() if "Legislativos" in x else x)

In [251]:
print(f"There are {inipros['comisiones'].nunique()} different commissions.")

There are 41 different commissions.


In [252]:
commissions = inipros['comisiones'].unique()

In [240]:
inipros[inipros["comisiones"]=="Salud"]["sintesis"].tolist()

['Propone crear los certificados de vacunación extraordinaria o por acción extraordinaria en materia de Salubridad General físicos o digitales.\r\n\r\nEstos se expedirán cuando las personas hayan obtenido las vacunas necesarias por la autoridad competente; en el caso de pandemia internacional, la Secretaría de Salud (SS), deberá coordinarse con la Secretaría de Relaciones Exteriores y la Secretaría de Gobernación para coordinar políticas de ingreso al país.\r\n\r\nAdemás, crea el Sistema Informático Nacional para la verificación y validez de estos certificados para los tramites que así lo requieran.\r\n\r\nFaculta a la SS para publicar un reglamento en el que se determinan los mecanismos, sistemas de seguridad, funcionamiento y obligaciones relacionadas.',
 'Propone establecer como materia de salubridad general la atención médica, preferentemente en beneficio de grupos vulnerables y la Protección Social la cual estará a cargo de la Secretaría de Salud.\r\n\r\nCrea el Sistema de Protecc

### Add list of initiative strings back to senator table

In [253]:
senators["initiative_list"] = ""

In [254]:
#Function that creates a list of initiative syntheses and then adds to senator database.
for i, row in senators.iterrows():
    initiatives = []
    relevant_inipros = inipros[inipros["senator_id"] == str(row["senator_id"])]["sintesis"]
    [initiatives.append(initiative.replace('\r\n\r\n', ' ')) for initiative in relevant_inipros]
    senators.at[i, "initiative_list"] = initiatives

In [255]:
#Creates dummy summary of a all initiatives, to be replaced by BERT or BETO summaries.
senators["initiatives_summary_dummy"] = senators["initiative_list"].apply(lambda x: "".join(x))

In [256]:
#Create column for each commission
for commission in commissions:
    senators[f"{commission}_initiative_list"] = ""

In [262]:
#Fill columns with relevant initiatves per sentator and commission
for i, row in senators.iterrows():
    print(row["senadores"])
    for commission in commissions:
        print(commission)
        initiatives = []
        relevant_inipros = inipros[(inipros["senator_id"] == str(row["senator_id"])) & (inipros["comisiones"]==str(commission))]["sintesis"]
        [initiatives.append(initiative.replace('\r\n\r\n', ' ')) for initiative in relevant_inipros]
        print(initiatives)
        senators.at[i, f"{commission}_initiative_list"] = initiatives

José Alfredo Botello Montes
Salud
[]
Justicia
['Propone establecer que el instituto de Servicios Periciales y Ciencias Forenses será el área técnica de apoyo a la Fiscalía que tendrá como objetivo fortalecer su capacidad institucional para realizar sus funciones de manera especializada y científica. Determina el establecimiento de un Servicio de Carrera Pericial.']
Estudios Legislativos
['Propone establecer que las iniciativas ciudadanas tengan el carácter de preferente.']
Seguridad Social
[]
Gobernación
[]
Educación
['Propone establecer que el Sistema Educativo Nacional considerará la educación en materia de privacidad y protección de sus datos personales en el ámbito digital, así que deberá ser incluida en los planes y programas de estudio.']
Para la Igualdad de Género
[]
Medio Ambiente, Recursos Naturales y Cambio Climático
[]
Defensa Nacional
[]
Anticorrupción, Transparencia y Participación Ciudadana
[]
Ciencia y Tecnología
[]
Asuntos Indígenas
[]
Energía
[]
Marina
[]
Agricultura, 

['Propone crear un reconocimiento denominado “Medalla de Honor Armada de México” misma que será otorgada por el Senado de la República para premiar a los hombres y mujeres mexicanos que se hayan distinguido por sus méritos académicos, profesionales, cívicos, su relevancia social, o cualquier otra circunstancia que la Comisión de Marina estime que constituyan acciones o hechos sobresalientes durante la prestación de los servicios que, ordinaria o extraordinariamente les sean encomendados. Además, se establecen las características que tendrá dicha Medalla, así como el procedimiento que el Senado de la República llevará a cabo a través de la mayoría simple de los integrantes de la Comisión de Marina para emitir la convocatoria pública para la postulación de candidaturas.']
Agricultura, Ganadería, Pesca y Desarrollo Rural
[]
Zonas Metropolitanas y Movilidad
[]
Comunicaciones y Transportes
[]
Seguridad Pública
[]
Reglamentos y Prácticas Parlamentarias
['Propone que las proposiciones con pun

['Propone que las personas titulares del Sistema Nacional de Salud tendrán la obligación de coordinar programas ininterrumpidos de difusión a todo el personal médico y de enfermería respecto a su derecho a la objeción de conciencia.', 'Propone establecer como obligación del Estado y todas las dependencias que pertenecen al Sistema Nacional de Salud, el informar a todas las mujeres sus derechos durante el embarazo, parto, postparto y puerperio, haciendo campañas de información ininterrumpidas.', 'Propone que, quede prohibida la publicidad y la venta de alimentos y bebidas con bajo valor nutricional y alta densidad energética, dentro de los centros escolares.', 'Propone que a quien niegue, limite o condicione el acceso a medicamentos o fármacos del Cuadro Básico o catálogo de medicamentos asignado a las instituciones del Sistema Nacional de Salud, le será impuesta una pena de uno a cinco años de prisión y multa equivalente de mil a veinte mil días de salario mínimo general vigente en la 

[]
Relaciones Exteriores
[]
Cámara de Diputados
[]
Urgente Resolución
[]
Junta de Coordinación Política
[]
Defensa de los Consumidores
[]
Puntos Constitucionales
['Propone establecer que la Suprema Corte de Justicia de la Nación tendrá el derecho de iniciar leyes o decretos en lo que se refiere a la estructura, organización y funcionamiento del poder judicial.']
Comunicaciones y Obras Públicas
['ÚNICO. La Comisión Permanente del Congreso de la Unión exhorta de manera respetuosa a la Secretaría de Hacienda y Crédito Público y a la Secretaría de Medio Ambiente y Recursos Naturales para que, en el ámbito de sus respectivas atribuciones y competencias, informen a esta soberanía sobre el posible impacto ante el recorte del 75% del presupuesto disponible en las partidas de materiales y suministros, así como, de servicios generales, a los organismos descentralizados y desconcentrados como son la Comisión Nacional Forestal (CONAFOR), Instituto Mexicano de Tecnología del Agua (IMTA), Instituto 

['Propone establecer un mecanismo de controversia en línea con el objeto de desahogar procedimientos conciliatorios a través de internet entre proveedores y consumidores.', 'Propone incluir al Instituto Nacional del Emprendimiento, con la finalidad de que pueda recuperar su estructura administrativa y presupuestal y llevar a cabo la implementación de programas, proyectos y políticas públicas especializadas en el fortalecimiento del sector de las MiPyMEs, además de establecer un fideicomiso para promover el Acceso al Financiamiento de las MiPyMEs y Personas Emprendedoras.', 'PRIMERO. -El Senado de la República, exhorta respetuosamente a la Secretaría de Economía, para que, en el ámbito de sus atribuciones, realice un estudio sobre la pertinencia de continuar con el Acuerdo por el que se da a conocer el Cupo para importar, con Arancel-Cupo Establecido, Carne de Pollo, publicado en el Diario Oficial de la Federación el 16 de mayo de 2013 y cuyo vencimiento acontecerá el 31 de diciembre de

...

['Propone expedir la Ley de la Cafeticultura con el objeto de normar, impulsar, fomentar y promover la producción, comercialización, industrialización, certificación y consumo del café. Crea el Consejo Mexicano del Café como organismo público descentralizado y fungirá como instancia de consulta para el Gobierno Federal en lo concerniente a la actividad cafetalera; así mismo, el Consejo contara con una Junta de Gobierno como órgano de dirección que estará presidido por el Titular de la Secretaría de Agricultura y Desarrollo Rural. El Consejo operara un Registro Nacional de Productores, Industriales, Comercializadores y Exportadores de Café como mecanismo de inscripción y consulta en lo relativo a este sector. Por otra parte, la Secretaría de Agricultura y Desarrollo Rural deberá formular el Plan Rector para el desarrollo de la Cafeticultura y el Ejecutivo Federal deberá prever en el proyecto de Presupuesto de Egresos de la Federación un Fondo de Estabilización, Fortalecimiento y Reorden

['Propone una ley de nueva creación que tiene por objeto garantizar la protección a las personas físicas o servidoras públicas, que presenten una alerta o una denuncia por un posible hecho de corrupción. Por lo que las personas alertadoras de un posible hecho de corrupción, una vez evaluado su caso por las autoridades investigadoras y determinado que esta podría estar vinculada con un posible hecho de corrupción, deberán recibir el ofrecimiento de ser integradas al Registro Federal de Protección de Personas Alertadoras y Denunciantes de Hechos Corrupción. Se crea un Sistema Federal de Alerta de la Corrupción y de Protección a Personas Alertadoras y Denunciantes el cual será el medio para recopilar, turnar, analizar e investigar la información proporcionada por las personas alertadoras y denunciantes de hechos corrupción, así como para determinar y brindar las medidas de protección necesarias.', 'PRIMERO. El Senado de la República exhorta respetuosamente a la Auditoría Superior de la Fe

['Propone regular las relaciones de trabajo de las personas trabajadoras del hogar definiéndolas como aquellas que de manera remunerada realicen actividades de cuidados, aseo, asistencia, o cualquier otra actividad inherente al hogar en el marco de una relación laboral que no aporte para la persona empleadora beneficio económico directo; no lo serán aquellas que realicen la actividad remunerada de manera ocasional o espontanea, ni que realicen estas actividades en otros lugares como en hoteles. Los empleadores deberán registrarse e inscribir a las personas trabajadoras del hogar en el IMSS y señalar los días en que laboraran durante el mes de aseguramiento y salario base de cotización; el aseguramiento iniciará el primer día del mes inmediato posterior a aquel que se haya efectuado el pago. La remuneración deberá pagarse de acuerdo con los formatos emitidos por el Instituto y se realizará los primeros 20 días de cada mes o al día siguiente si no es hábil. En el caso de incapacidades el

[]
Mesa Directiva
[]
Héctor Vasconcelos
Salud
['Propone que sea declarado el 28 de junio de cada año el “Día Nacional de los Tamices Neonatales” con el objeto de homologar la concientización de la realización de esta prueba a nivel internacional con el objeto de sensibilizar al respecto y seguir trabajando por los derechos y la salud de las y los recién nacidos.']
Justicia
['Propone expedir la Ley General de Mecanismos Alternativos de Solución de Controversias que tiene por objeto regular las bases del Sistema de Justicia Alternativa, que tendrá a su cargo la aplicación de los mecanismos alternativos de solución de controversias, como vías para la gestión pacífica y colaborativa de los conflictos, previo al proceso o en cualquier etapa del proceso jurisdiccional. Además, propone establecer la integración del sistema de justicia alternativa, los procedimientos para acceder a esta y la organización y funcionamiento de los centros de justicia alternativa.', 'PRIMERO. El Senado de la Repúb

['PRIMERO. - El Senado de la República exhorta respetuosamente a los Titulares Secretaría de Medio Ambiente y Recursos Naturales (SEMARNAT), y a la Comisión Nacional de Áreas Naturales Protegidas (CONANP), para que en el ámbito de sus atribuciones respectivamente, informen a esta Soberanía sobre las acciones jurídicas realizadas o por realizar para negar la autorización del proyecto de desarrollo inmobiliario turístico de 21 mil cuartos de hotel en el Área de Protección de Flora y Fauna “Yum Balam”, ubicado en la Isla de Holbox, en el estado de Quintana Roo.  \r\nSEGUNDO. - El Senado de la República exhorta respetuosamente a la Procuraduría Federal de Protección al Ambiente (PROFEPA), para que en el ámbito de sus atribuciones informe a esta Soberanía sobre las violaciones normativas que cometió la construcción del proyecto hotelero y de acuerdo con éstas clausure la autorización del desarrollo inmobiliario turístico de 21 mil cuartos de hotel en el Área de Protección de Flora y Fauna “

### Export file to CSV in data folder

In [189]:
senators.to_csv(r'/Users/jmlunamugica/code/jomilu93/sivico/senators_data.csv')

# Classifying initiatives & proposals into topics with LDA (DEPRECATED)

## LDA Approach

### Preprocessing text

In [244]:
import string
from nltk.corpus import stopwords 
from nltk import word_tokenize
from nltk.stem import WordNetLemmatizer
import re

In [257]:
def clean(column):
    """Remove punctuation, make strings lower case, remove numbers. Tokenize, remove stopwords and lemmatize."""
    #Removing punctuation.
    for punctuation in string.punctuation:
        column = column.apply(lambda x: x.replace(punctuation, ''))
    #Making lower case and removing whitespace.
    column = column.apply(lambda x: x.lower().strip())
    #Removing numbers
    column = column.apply(lambda x: re.sub(r'[0-9]', '', x))
    #Tokenize all rows.
    column = column.apply(lambda x: word_tokenize(x))
    #Remove stopwords and words too frequently present in initiative language.
    stop_words = set(stopwords.words('spanish'))
    stop_words_extra = ("exhorta", "modificar", "actualizar", "política", "general", "caso", "derecho", "materia", "virtud", "referencias", "cambiar", "deberán", "día", "año", "denominación", "distrito", "cámara", "senadores", "normativa", "senado", "objetivo", "cumplimiento", "ordenamiento", "república", "reforma", "cada", "dar", "federal", "secretaría", "mención", "paso", "dejar", "principio", "ser", "paridad", "así", "derechos", "reformar", "propone", "nacional", "establecer", "méxico", "persona", "ley", "ciudad", "deberá", "legal", "personas")
    column = column.apply(lambda x: [w for w in x if w not in stop_words])
    column = column.apply(lambda x: [w for w in x if w not in stop_words_extra])
    # Lemmatizing the verbs
    column = column.apply(lambda x: [WordNetLemmatizer().lemmatize(word, pos = "v") for word in x])
    # 2 - Lemmatizing the nouns
    column = column.apply(lambda x: [WordNetLemmatizer().lemmatize(word, pos = "n") for word in x])
    # Rejoin words to make sentences
    column = column.apply(lambda x: " ".join(x))
    return column

In [258]:
inipros["sintesis_clean"] = clean(inipros["sintesis"])

### Training vectorization model

In [252]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation

In [259]:
vectorizer = TfidfVectorizer()

vectorized_text = vectorizer.fit_transform(inipros["sintesis_clean"])

# Instantiate the LDA 
n_components = 15
lda_model = LatentDirichletAllocation(n_components=n_components)

# Fit the LDA on the vectorized documents
lda_model.fit(vectorized_text)

LatentDirichletAllocation(n_components=15)

### Visualize potential topics

In [255]:
def print_topics(model, vectorizer):
    for idx, topic in enumerate(model.components_):
        print("Topic %d:" % (idx))
        print([(vectorizer.get_feature_names_out()[i], topic[i]) for i in np.argsort(topic)[:-5 -1:-1]])

In [260]:
print_topics(lda_model, vectorizer)

Topic 0:
[('cuidados', 8.152377824370088), ('plazo', 6.54867271043552), ('moratorios', 6.251462236713305), ('tratándose', 6.140648831027995), ('circuito', 5.822456621174861)]
Topic 1:
[('prisión', 17.33962346795972), ('delitos', 15.172324267906053), ('delito', 15.069667077986509), ('votos', 14.898576003258666), ('democrática', 14.693022763766855)]
Topic 2:
[('inclusivo', 18.261246187847167), ('lenguaje', 17.418572834911885), ('constitucionales', 16.878337552432512), ('disposiciones', 15.727013331203173), ('incorporar', 14.849857208397227)]
Topic 3:
[('órganos', 17.763659837930643), ('federales', 15.273162946841973), ('uso', 11.773341107108418), ('tribunales', 10.711978953185039), ('administrativos', 10.623157522217339)]
Topic 4:
[('indígenas', 34.68765761725618), ('pueblo', 30.01337346202277), ('agua', 27.900267103930567), ('ordenamientos', 27.526534543323102), ('inclusión', 25.80922310283219)]
Topic 5:
[('género', 90.26950785407557), ('garantizar', 76.29735575292742), ('salud', 15.686

### Test with real initiatives

In [267]:
random_num = np.random.randint(0, len(inipros))
example = [inipros["sintesis"][random_num]]
example_df = pd.DataFrame(example, columns = ["text"])
print(example_df["text"][0])

ÚNICO. El Senado de la República exhorta respetuosamente la Secretaria de Comunicaciones y Transportes, para que, en el marco de sus atribuciones, revise las tarifas que se cobran en las carreteras de cuota, con la finalidad de evitar cobros excesivos que afecten la economía de los usuarios, y se mejore y mantenga el estado físico de la red carretera del país.


In [268]:
clean_example = clean(example_df["text"])
example_vectorized = vectorizer.transform(clean_example)
lda_vectors = lda_model.transform(example_vectorized)
lda_vectors

array([[0.01157094, 0.01157095, 0.01157098, 0.01157095, 0.01157094,
        0.01157095, 0.30414982, 0.01157098, 0.01157097, 0.01157095,
        0.01157095, 0.01157097, 0.01157104, 0.01157097, 0.54542765]])